# Using Medical Image Segmentations MME

Please cite us if you use our codes or ideas ;)
```
@misc{modaresi2022mis,
  doi = {10.34740/KAGGLE/DSV/4728423},
  url = {https://www.kaggle.com/dsv/4728423},
  author = {{Seyed Modaresi} and {Aomar Osmani} and {Mohammadreza Razzazi} and {Abdelghani Chibani}},
  title = {Medical Image Segmentation: Evaluation},
  publisher = {Kaggle},
  year = {2022}
}
```


## Install Dependencies

In [1]:
!pip install -U --progress-bar on -q evalseg==2.0.8

# for installing latest version from github
# !pip uninstall -y evalseg 
# !pip install -U --progress-bar on  git+https://github.com/modaresimr/evalseg.git

# Import

In [2]:
import evalseg
import numpy as np
import pandas as pd
from ipywidgets import interact, IntSlider
import os

## Variables

In [3]:
root_data='/kaggle/input/medical-image-segmentation/'

## Run Metric


In [4]:
@interact
def select_dataset(dataset_name=sorted([d for d in os.listdir(root_data) if os.path.isdir(f'{root_data}/{d}')])):
    global dataset
    evalseg.reload()
    dataset = evalseg.io.Dataset(f'{root_data}/{dataset_name}')

    @interact
    def select_case(case=sorted(dataset.get_available_ids())):
        gto = dataset.get_groundtruth(case)
        cto = dataset.get_CT(case)
        if cto is None: cto=gto
        gtmax = evalseg.geometry.calc_max_slice_idx(gto)

        @interact
        def axselect(ax=['z', 'x', 'y','all']):
            axi = {'all': -1, 'x': 0, 'y': 1, 'z': 2}[ax]
            @interact
            def onlyMaxFrame(frame=IntSlider(-1,min=-1,max=-1) if ax=='all' else IntSlider(gtmax[axi], min=0, max=gto.shape[axi]-1)):
                global data, gt,ct, voxelsize
                gt = evalseg.geometry.slice_segment(gto, axi, [frame])
                ct = evalseg.geometry.slice_segment(cto, axi, [frame])
                data = {p: evalseg.geometry.slice_segment(dataset.get(p, case), axi, [frame]) for p in dataset.get_prediction_methods()}
                ctlbl = f"{dataset_name.split('_')[1]} {case}"
                if ax!='all':
                    ctlbl = f"{ctlbl} {ax}={frame}"
                    evalseg.ui.multi_plot_2d(ct, gt, data, spacing=gt.voxelsize, ctlbl= ctlbl, z_titles= [frame])
                else:
                    @interact
                    def visualize3d(pred=sorted(dataset.get_prediction_methods(case))):
                        pred_data=data[pred]
                        multi_plot=evalseg.ui3d.plot_3d(ct.todense(), gt.todense(), 
                                 pred_data.todense(),
                                 spacing=gt.voxelsize,zoom2segments=0,
                                 scaledown=(3,3,3),
                                 show_ct=False,
                                 show_gt=0,
                                 show_pred=1
                                 )
                    print('Kaggle do not support 3D viewer. Please run it in your own jupyter notebook.')
        
                mme = evalseg.metrics.MultiClassMetric(evalseg.metrics.MME,dataset.num_labels)
                mme.set_reference(gt)
                res = mme.evaluate_multi(data)
                evalseg.ui.plot_metric_multi(res, name=dataset_name)


interactive(children=(Dropdown(description='dataset_name', options=('Task001_LiverTumor', 'Task002_Pancreas', …